# Statistics for Performance Engineers I: Descriptive Statistics and Visualization

The following is the accompanying notebook for my learning paper: "Statistics For Performance Engineers I: Descriptive Statistics and Visualization".

In [ ]:
#r "nuget: Newtonsoft.Json"
#r "nuget: XPlot.Plotly"
#r "nuget: XPlot.Plotly.Interactive"
#r "nuget: BenchmarkDotNet"
#r "nuget: MathNet.Numerics"

using Newtonsoft.Json;
using XPlot.Plotly;
using System.IO;
using MathNet.Numerics;
using MathNet.Numerics.Distributions;
using MathNet.Numerics.Statistics;

Installed Packages BenchmarkDotNet, 0.13.2 MathNet.Numerics, 5.0.0 Newtonsoft.Json, 13.0.1 XPlot.Plotly, 4.0.6 XPlot.Plotly.Interactive, 4.0.6

Loading extensions from `XPlot.Plotly.Interactive.dll`

Configuring PowerShell Kernel for XPlot.Plotly integration.

Installed support for XPlot.Plotly.

## Why Should A Performance Engineer Learn About Statistics?

In [ ]:
public class ErrorY
{
    public string type { get; set; }
    public List<double> array { get; set; }
    public bool visible { get; set; }
}

public class BenchmarkData 
{
    public List<DateTime> x { get; set; }
    public List<double> y { get; set; }
    public List<string> gitHashruntime { get; set; }
    public string name { get; set; }
    public ErrorY error_y { get; set; }
    public List<string> perfRepoHash { get; set; }
    public string visible { get; set; }
}

In [ ]:
List<BenchmarkData> doubleMax = JsonConvert.DeserializeObject<List<BenchmarkData>>(File.ReadAllText(Path.Combine("./Data", "Double.Max_Windows10_x64.json")));
BenchmarkData benchmarkResults = doubleMax[0];

### 1. Comparing a Real World vs. Theoretical Distributions

In [ ]:
List<double> y = benchmarkResults.y;
IEnumerable<double> normalizedY = y.Select(d => ( d - y.Average() ) / y.StandardDeviation() );

var layout = new Layout.Layout
{
    title = "Comparing A Real World Distribution with the Normal Distribution"
};

var doubleMaxHistogram = new XPlot.Plotly.Histogram
{
    x = normalizedY,
    name = "ZScore Normalized Benchmark: Double.Max" 
};

var normalHistogram = new XPlot.Plotly.Histogram
{
    x = Normal.Samples(mean: 0, stddev: 1).Take(1000),
    name = "Standard Normal Distribution"
};

Chart.Plot(new [] { doubleMaxHistogram, normalHistogram }, layout)

<!DOCTYPE html>

### 2. Knowing when you need more data, or if your experiment needs to be changed 

In [ ]:
var lowSampleSizeNormalDistribution = Normal.Samples(mean: 0, stddev: 1).Take(10);

var layout = new Layout.Layout
{
    title = "Low Sample Size Normal Distribution (n = 10)"
};

var lowSampleSizeNormalHistogram = new XPlot.Plotly.Histogram
{
    x = lowSampleSizeNormalDistribution, 
};

Console.WriteLine($"Standard Error: {lowSampleSizeNormalDistribution.StandardDeviation() / Math.Sqrt(lowSampleSizeNormalDistribution.Count())}");
Chart.Plot(lowSampleSizeNormalHistogram, layout)

Standard Error: 0.26456271316902447


<!DOCTYPE html>

In [ ]:
var highSampleSizeNormalDistribution = Normal.Samples(mean: 0, stddev: 1).Take(10000);

var layout = new Layout.Layout
{
    title = "High Sample Size Normal Distribution (n = 10,000)"
};

var highSampleSizeNormalHistogram = new XPlot.Plotly.Histogram
{
    x = highSampleSizeNormalDistribution, 
};

Console.WriteLine($"Standard Error: {highSampleSizeNormalDistribution.StandardDeviation() / Math.Sqrt(highSampleSizeNormalDistribution.Count())}");
Chart.Plot(highSampleSizeNormalHistogram, layout)

Standard Error: 0.010028870777494415


<!DOCTYPE html>

## Descriptive Statistics

### Sample Size

In [ ]:
List<(double mean, double sampleSize)> data = new();
int n = 1000;

for(int i = 1; i < n; i++)
{
    var samples = Normal.Samples(mean: 0, stddev: 1).Take(i);
    data.Add((mean: samples.Mean(), sampleSize: i));
}

var layout = new Layout.Layout
{
    title = "How Sample Size Increases Affect the Mean",
    xaxis = new Xaxis { title = "Number of Samples (n)" },
    yaxis = new Yaxis { title = "Mean" }
};

var scatter = new Scatter
{
    x = data.Select(d => d.sampleSize), 
    y = data.Select(d => d.mean),
};

Chart.Plot(scatter, layout)

<!DOCTYPE html>

### Minimum, Maxmium and Range

In [ ]:
var layout = new Layout.Layout
{
    title = "How Variance Affects Min., Max. and the Range",
    xaxis = new Xaxis { title = "Number of Samples (n)" },
    yaxis = new Yaxis { title = "Mean" }
};

var scatter = new Scatter
{
    x = data.Select(d => d.sampleSize), 
    y = data.Select(d => d.mean),
};

Chart.Plot(scatter, layout)

<!DOCTYPE html>

### 5 Number Summary via a BoxPlot

In [ ]:
var normalDistribution1 = Normal.Samples(mean: 0, stddev: 1).Take(10000).ToList();
var normalDistribution2 = Normal.Samples(mean: 4, stddev: 1).Take(10000);

var layout = new Layout.Layout
{
    title = "Box Plots"
};

var box1 = new Box
{
    y = normalDistribution1,
    name = "Box Plot 1"
};

var box2 = new Box
{
    y = normalDistribution2,
    name = "Box Plot 2"
};

Chart.Plot(new [] { box1, box2 }, layout)

<!DOCTYPE html>

### Mode

#### Unimodal

In [ ]:
var normalDistribution = Normal.Samples(mean: 0, stddev: 1).Take(10000);

var layout = new Layout.Layout
{
    title = "Unimodal Distribution"
};

var unimodal = new XPlot.Plotly.Histogram
{
    x = normalDistribution, 
};

Chart.Plot(unimodal, layout)

<!DOCTYPE html>

#### Bimodal

In [ ]:
var normalDistribution1 = Normal.Samples(mean: 0, stddev: 1).Take(10000).ToList();
var normalDistribution2 = Normal.Samples(mean: 4, stddev: 1).Take(10000);
normalDistribution1.AddRange(normalDistribution2);

var layout = new Layout.Layout
{
    title = "Bimodal Distribution"
};

var bimodal = new XPlot.Plotly.Histogram
{
    x = normalDistribution1, 
};

Chart.Plot(bimodal, layout)

<!DOCTYPE html>

#### Multimodal

In [ ]:
var normalDistribution1 = Normal.Samples(mean: 0, stddev: 1).Take(10000).ToList();
var normalDistribution2 = Normal.Samples(mean: 4, stddev: 1).Take(10000);
var normalDistribution3 = Normal.Samples(mean: -4, stddev: 1).Take(10000);
normalDistribution1.AddRange(normalDistribution2);
normalDistribution1.AddRange(normalDistribution3);

var layout = new Layout.Layout
{
    title = "Multimodal Distribution"
};

var bimodal = new XPlot.Plotly.Histogram
{
    x = normalDistribution1, 
};

Chart.Plot(bimodal, layout)

<!DOCTYPE html>

### Standard Deviation and Variance

In [ ]:
var highSpread = Normal.Samples(mean: 0, stddev: 10).Take(10_000);
var lowSpread  = Normal.Samples(mean: 0, stddev: 0.1).Take(10_000);

var layout = new Layout.Layout
{
    title = "High Spread vs. Low Spread Distribution",
    barmode = "stack"
};

var highSpreadHistogram = new XPlot.Plotly.Histogram
{
    x = highSpread,
    name = "High Spread"
};

var lowSpreadHistogram = new XPlot.Plotly.Histogram
{
    x = lowSpread, 
    name = "Low Spread"
};


Chart.Plot(new [] { highSpreadHistogram, lowSpreadHistogram }, layout)

<!DOCTYPE html>

### Skewness

#### Right Skewness

In [ ]:
var normalDistribution = Normal.Samples(mean: 0, stddev: 1).Take(10000);
var rightSkewed = normalDistribution.Select(d => d * d);

var layout = new Layout.Layout
{
    title = "Right Skewed Distribution"
};

var rightSkewedHistogram = new XPlot.Plotly.Histogram
{
    x = rightSkewed, 
};

Chart.Plot(rightSkewedHistogram, layout)

<!DOCTYPE html>

#### Left Skewness

In [ ]:
var normalDistribution = Normal.Samples(mean: 0, stddev: 1).Take(10000);
var leftSkew = normalDistribution.Select(d => Math.Log(d));

var layout = new Layout.Layout
{
    title = "Left Skewed Distribution"
};

var leftSkewedHistogram = new XPlot.Plotly.Histogram
{
    x = leftSkew, 
};

Chart.Plot(leftSkewedHistogram, layout)

<!DOCTYPE html>

#### Zero Skewness

In [ ]:
var normalDistribution = Normal.Samples(mean: 0, stddev: 1).Take(10000);

var layout = new Layout.Layout
{
    title = "Zero Skewed Distribution"
};

var zeroSkewedDistribution = new XPlot.Plotly.Histogram
{
    x = normalDistribution,
};

Chart.Plot(zeroSkewedDistribution, layout)

<!DOCTYPE html>

### Kurtosis

In [ ]:
var stdNormalDistribution = Normal.Samples(mean: 0, stddev: 1).Take(100_000);
var leptokurticNormalDistribution = Normal.Samples(mean: 0, stddev: 0.7).Take(100_000);
var platykurticNormalDistribution = ContinuousUniform.Samples(lower: -3, upper: 3).Take(100_000);

var layout = new Layout.Layout
{
    title = "Different Types of Kurtosis",
    showlegend = true,
};

var zeroKurtosis = new XPlot.Plotly.Histogram
{
    x = stdNormalDistribution,
    name = "Zero Kurtosis",

};

var leptokurtic = new XPlot.Plotly.Histogram
{
    x = leptokurticNormalDistribution,
    name = "Leptokurtic - Positive Kurtosis",
};

var platykurtic = new XPlot.Plotly.Histogram
{
    x = platykurticNormalDistribution, 
    name = "Platykurtic - Negative Kurtosis",
};

Chart.Plot(new [] { zeroKurtosis, leptokurtic, platykurtic }, layout)

<!DOCTYPE html>

## Visualization

### Line Chart

In [ ]:
var layout = new Layout.Layout
{
    title = "Comparative Line Chart"
};

var x0 = new [] { DateTime.Today.AddDays(-6),  DateTime.Today.AddDays(-5),  DateTime.Today.AddDays(-4),  DateTime.Today.AddDays(-3),  DateTime.Today.AddDays(-2) };
var y0 = ChiSquared.Samples(5).Take(x0.Count());

var scatter0 = new Scatter
{
    x = x0, 
    y = y0
};

var x1 = new [] { DateTime.Today.AddDays(-6),  DateTime.Today.AddDays(-5),  DateTime.Today.AddDays(-4),  DateTime.Today.AddDays(-3),  DateTime.Today.AddDays(-2) };
var y1 = ChiSquared.Samples(5).Take(x0.Count());

var scatter1 = new Scatter
{
    x = x1, 
    y = y1
};

Chart.Plot(new [] { scatter0, scatter1 }, layout)

<!DOCTYPE html>

### Area Chart 

In [ ]:
var layout = new Layout.Layout
{
    title = "Comparative Area Chart"
};

var x0 = new [] { DateTime.Today.AddDays(-6),  DateTime.Today.AddDays(-5),  DateTime.Today.AddDays(-4),  DateTime.Today.AddDays(-3),  DateTime.Today.AddDays(-2) };
var y0 = ChiSquared.Samples(5).Take(x0.Count());

var scatter0 = new Scatter
{
    x = x0, 
    y = y0,
    fill = "tozeroy",
    name = "Series 1"
};

var x1 = new [] { DateTime.Today.AddDays(-6),  DateTime.Today.AddDays(-5),  DateTime.Today.AddDays(-4),  DateTime.Today.AddDays(-3),  DateTime.Today.AddDays(-2) };
var y1 = ChiSquared.Samples(5).Take(x0.Count());

var scatter1 = new Scatter
{
    x = x1, 
    y = y1,
    fill = "tonexty",
    name = "Series 2"
};

Chart.Plot(new [] { scatter0, scatter1 }, layout)

<!DOCTYPE html>

### Bubble Chart

In [ ]:
var trace1 = new Scatter
{
    x = new [] { 1,2,3,4 },
    y = new [] { 10, 11, 12, 13 },
    name = "Series 1"
    mode = "markers",
    marker = new Marker
    {
        color = "red",
        size = new [] { 12, 22, 32, 42 }
    }
};

var trace2 = new Scatter 
{
    x = new [] { 1,2,3,4 },
    y = new [] { 10, 11, 12, 16 },
    mode = "markers",
    marker = new Marker
    {
        color = "blue",
        size = 18, 
    }
};

Chart.Plot(new [] { trace1, trace2 })

<!DOCTYPE html>

### Bar Chart

##### Unstacked

In [ ]:
var layout = new Layout.Layout
{
    title = "Bar Chart Comparing Regressions vs. Improvements vs. Stale Results"
};

List<(string category, double results)> categoricalResults_Experiment1 = new() 
{
    ( "Regressions", 23 ),
    ( "Improvements", 10 ),
    ( "Stale", 5 ),
};

List<(string category, double results)> categoricalResults_Experiment2 = new() 
{
    ( "Regressions", 10 ),
    ( "Improvements", 23 ),
    ( "Stale", 5 ),
};


var barChart_Experiment1 = new Bar
{
    x = categoricalResults_Experiment1.Select(c => c.category),
    y = categoricalResults_Experiment1.Select(c => c.results),
    name = "Experiment 1"
};

var barChart_Experiment2 = new Bar
{
    x = categoricalResults_Experiment2.Select(c => c.category),
    y = categoricalResults_Experiment2.Select(c => c.results),
    name = "Experiment 2"
};


Chart.Plot(new [] { barChart_Experiment1, barChart_Experiment2 }, layout)


<!DOCTYPE html>

#### Stacked

In [ ]:
var layout = new Layout.Layout
{
    title = "Bar Chart Comparing Regressions vs. Improvements vs. Stale Results - Stacked",
    barmode = "stack"
};

List<(string category, double results)> categoricalResults_Experiment1 = new() 
{
    ( "Regressions", 23 ),
    ( "Improvements", 10 ),
    ( "Stale", 5 ),
};

List<(string category, double results)> categoricalResults_Experiment2 = new() 
{
    ( "Regressions", 10 ),
    ( "Improvements", 23 ),
    ( "Stale", 5 ),
};


var barChart_Experiment1 = new Bar
{
    x = categoricalResults_Experiment1.Select(c => c.category),
    y = categoricalResults_Experiment1.Select(c => c.results),
    name = "Experiment 1"
};

var barChart_Experiment2 = new Bar
{
    x = categoricalResults_Experiment2.Select(c => c.category),
    y = categoricalResults_Experiment2.Select(c => c.results),
    name = "Experiment 2"
};


Chart.Plot(new [] { barChart_Experiment1, barChart_Experiment2 }, layout)


<!DOCTYPE html>

### Scatterplot

In [ ]:
var first = Normal.Samples(mean: 0, stddev: 1).Take(100);
var second = Normal.Samples(mean: 0, stddev: 19).Take(100);

var layout = new Layout.Layout
{
    title = "Scatter of 2 different variables"
};

var scatter1 = new Scatter
{
    x = Enumerable.Range(0, 100),
    y = first,
    mode = "markers",
    name = "Scatter - 1"
};

var scatter2 = new Scatter
{
    x = Enumerable.Range(0, 100),
    y = second,
    mode = "markers",
    name = "Scatter - 2"
};

Chart.Plot(new [] { scatter1, scatter2 }, layout)

<!DOCTYPE html>

### Heat Map

In [ ]:
var values = new List<List<double>>(5)
{
    new List<double>{ 1, 20, 30 },
    new List<double>{ 20, 1, 60 },
    new List<double>{ 30, 60, 1 },
};

var layout = new Layout.Layout
{
    title = "Example Heat Map"
};

var heatMap = new XPlot.Plotly.Heatmap()
{
    z = values
};

Chart.Plot(heatMap, layout)

<!DOCTYPE html>

In [ ]:
#!about

<img src="data:image/png;base64, iVBORw0KGgoAAAANSUhEUgAAAcgAAAHICAYAAADKoXrqAAAACXBIWXMAAAsTAAALEwEAmpwYAAAAAXNSR0IArs4c6QAAAARnQU1BAACxjwv8YQUAAA5XSURBVHgB7d1frNd1HcfxjyYNwUOUcUbiBaxWbHQbXoNb3dCwrcFNXhyuGmk3XcBWeWG2xUVXFnkFW3rD5pYuvHETug1ucVM3B6vB6DjSYJjhkn6fn2GkrwPn/M7n+/v7eGxMN5nTo5wn38/v+35/7vnejnM3CwBwu5v3FgDgMwQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAAKBBIBAIAEgEEgACAQSAIL7ChPtuVe/XuYfWlNaO3f2enlq4UKZZju+tb784vjW0sIPv/1WWbz0YenS/oObej/my6xZvPhh+eF33rrrz+vq18IsO/2Hd8uzP79UZpUnSKJv9uKx5/EvFYBZJZAsqT6t+B05MKsEkiWtn/tcWTi8uQDMIoHkjh7ZvaF33LquAMwageSunnjm4f7TJMAsEUjuan7LmrLv4KYCMEsEkmX57uMPOmoFZopAsmz7ZnAGD5hdAsmymY0EZolAsiJmI4FZIZCsSH2b9YlfbikA004gWbF61Lpz91wBmGYCyUAOHPqK2UhgqgkkAzEbCUw7gWRgZiOBaeY+SFZloXfU+pPvv12YLNev/bucf+ODMgneuXhjWT/vQu/fZ3GZP7cr27avbfbRw+KlG/27MEfp/Jv/KrNMIFmV+g2hzkaefP7vhclR4zhtF2L/6sd/KaP29PGt/ZfYWjj90nvlxNF3CqPjiJVVMxsJTCOBZNXMRgLTSCBpwmwkMG0Ekmae7D1Fmo0EpoVA0kyNo9lIYFoIJE2ZjQSmhUDSd+7s9dJKnY0EmHQCSd/xI5dLK3U2cr+jVmDCCSR9mx5aU868dq20sqd31Go2EphkAklffcHmjy9cKa2YjQQmnUDSt37DveX13ueQLT+LrLORu/ZuLACTSCDpuzW/+JufXSwtHTi82WwkMJEEkv9Tbw9ouXjcbCQwqQSSvnW3PeWdOLrYv2qnFbORwCQSSPoemPvf/wr1rsBnf3qptPTEMw87agUmikAS1Rd2zpy6WlqZ37Kmf28kwKQQSJZ07Mjl/tNkK2YjgUkikCypvrBz4rftbjQ3GwlMEoHkjk6+cKX5bKSjVmASCCR31Xo2cv/BeS/sAGNPILmr/lHr0bZHrQuHNheAcSaQLMvJ5680nY3c/dhGs5HAWBNIlsVsJDBrBJJlq7ORLdfQmY0ExplAsiJ1DV3L2cj6wo7ZSGAcCSQr0slRq9lIYAwJJCtWV9CZjQSmnUAykDob2fqo1Qs7wDgRSAbSzRq6hwrAuBBIBtZ6Dd0juzeYjQTGhkCyKsePXC4tmY0ExoVAsirn3/jAbCQwle4rsEp1NnLnow+U+Yc+X1qoL+z8+dS1cqEXX7qxbfva8vTxrWVcnX7pvXL65fcKjJJAsmq3ZiN/0fAb7oFDm8tTCxcK3ajH2HW8Zly93vCzbRiUI1aaqN/Q6u/6WzEbCYyaQNLMsSOXraEDpoZA0kyNY+vZyIXD7o0ERkMgacpsJDAtBJLmWq+hMxsJjIJA0lxdQ9d6NnLfwU0FYJgEkk7U2cjzDecYv/v4g45agaESSDpzrPEaun0H5wvAsAgknamzkS2PWs1GAsMkkHSqHrUuXrpRWjEbCQyLQNKpW2voWvn43sgtBaBrAknn6lHrmVNXSyv1qHXn7rkC0CWBZCjqU2TL2cgDh75iNhLolEAyFK3X0JmNBLrmuiuGpq6h2/noXLNrlups5Nne0e25s+8XVqb+huX6tY/KuLp+dXz/2ZgdAslQ1TV0v37xq82ORxd6R60/+f7bhZWpSxzctwl35oiVoWq9hm7b9rVmI4FOCCRDZzYSmAQCyUiYjQTGnUAyEl2soTMbCbQkkIxM66PWJ3tPkWYjgVYEkpGpowbHfvW30kqNo9lIoBWBZKTO9OcYr5dW3BsJtCKQjFydjWy5hq7ORgKslkAycnU2suUaujobud9RK7BKAslYqGvoWh617ukdtZqNBFZDIBkbx49cLq2YjQRWSyAZG3U/6Imj7Y5a62zkrr0bC8AgBJKxcvL5K01nIw8c3mw2EhiIQDJW6tusrdfQmY0EBiGQjJ3Wa+jMRgKDEEjGUl1D13I28olnHv7MUev7V9v9/YHpI5CMpdZHrfNb1nzm3siWAQamj0AytlqvoTMbCayEQDLWWq6h+/Rs5PVrHxWApQgkY631Gro6G3nrqNURK3AnAsnYa72Gbv/B+U9e2BFJYCkCyURouWHn9tlIx6zAUgSSidDVbOTixXZbe4DpIpBMjDob2XIN3b7eUes7vc84ARKBZGK0no2sL+zs6P0ASASSiVKPWk+/9F5ppS4QAEgEkolz7Mhlb58CnRNIJk6NY8vZSIBEIJlIrWcjAT5NIJlYLdfQAXzafYUVWT93b9m194tlx851Zdv2+z9Zfl0Hzs+/8c/+arQ/vfxu7+nm/UK36te6zkbudyEy0AGBXKYaxnobxJ7Hv9z/8/TX69hA+VYpux/b+PEO0aOL5fTL7d645LPq13jn7rneb1bWFoCWHLEuQ31K/PWLX/vvDs/lfcnq+MCTv9xSFg5tLnSrvtUK0JonyLuocXz6+LaB5+XqSrP6dHPkx3/1eVlHbq2h+/SFyCxt/YbPTeTdmPXXkP25DItA3sFq43hLPXpdOLy5/OanFwvd6B+1PvpA77/Z5wt3t+0ba8tzr369TJr637nl4nq4E0esd1B3dbbatLJ770ZPOB1qvYYOQCCXUHd01pdtWrr9HkLaq0etZ05dLQAtCOQS9vzgwdJajeOux75Q6I41dEArArmERx6dK134ptsjOtUfr7GGDmhAIIMur0Da+o37C92yhg5oQSCDLj8ndL3ScNQ1dACrIZDB+g2+LJPu401GjlqBwSlBUL+5MvlOPn+lLF66UQAGIZDBOxe7+6Z6/s0PCsNhNhJYDYEMFi992P/RhXNnvDwyTLfW0AGslEAu4fRL3dzC8coLVwrDVdeTmY0EVkogl1A/v2r9TbVG1+ebw+eoFRiEQC6h9TfV+rLIid8tFkajrqAzGwmshEDeQf2m2mJUoMa2Xnfl6XG06myko1ZguQTyLlZ7vU59cnxq4UI5/4a